In [1]:
import pandas as pd
import os
import seaborn as sns
from sklearn.metrics import classification_report
from sklearn.model_selection import train_test_split
from catboost import CatBoostClassifier
import warnings
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import f1_score
import numpy as np
import matplotlib.pyplot as plt
import optuna

warnings.filterwarnings('ignore')
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 100)
pd.set_option('float_format', '{:f}'.format)

In [2]:
data_train = pd.read_parquet('../data/processed/train_update.gzip').dropna(how='any')
data_sub = pd.read_parquet('../data/processed/test_update.gzip')

data_train.columns = [col.replace('-', '_') for col in data_train.columns]
data_sub.columns = [col.replace('-', '_') for col in data_sub.columns]

print(len(data_train.columns))

392


In [3]:
print(data_train.isna().sum().sum())
print(data_sub.isna().sum())

0
ID                          0
TARGET                  60789
CO_TIPO_SEXO                0
EDAD                        0
NO_DEPARTAMENTO             0
                        ...  
SALDO_VENCIDO_202305        0
SALDO_VENCIDO_202306        0
SALDO_VENCIDO_202307        0
SALDO_VENCIDO_202308        0
SALDO_VENCIDO_202309        0
Length: 392, dtype: int64


In [4]:
data_sub_id = data_sub[['ID']]

categorical_feats = ['CO_TIPO_SEXO', 'NO_DEPARTAMENTO', 'REGION', 'NO_PROVINCIA',
                     'SALDO_PEQ_EMP_FLAG_any', 'SALDO_MED_EMP_FLAG_any', 'SALDO_MIC_EMP_FLAG_any',
                     'CANT_EMP_NEG_FLAG_any','CANT_EMP_CONS_FLAG_any', 'CANT_EMP_HIPOT_FLAG_any',
                     ]
for col in categorical_feats:
    data_train[col] = data_train[col].astype('category')
    data_sub[col] = data_sub[col].astype('category')

TARGET_VAR = 'TARGET'
N_FOLDS = 5
N_JOBS = os.cpu_count() // 2.5

In [5]:

unselected_cols = [
'ID',
'SALDO_MED_EMP_mean',
'CANT_EMP_DOL_HIPOT_last',
'CANT_EMP_DOL_HIPOT_max',
'VAR_SALDO_DOLA_TOTAL_MA8_mean',
'CANT_EMP_DOL_NEG_first',
'SALDO_MED_EMP_median',
'PROXY_MOROSIDAD_2_median',
'SALDO_MED_EMP_last',
'SALDO_HIPOT_mean',
'SALDO_MED_EMP_max',
'SALDO_DOLA_HIPOT_max',
'SALDO_MED_EMP_first',
'SALDO_DOLA_NEG_min',
'SALDO_DOLA_HIPOT_min',
'CANT_EMP_DOL_NEG_last',
'SALDO_DOLA_NEG_first',
'CANT_EMP_DOL_HIPOT_min',
'SALDO_MED_EMP_min',
'CANT_EMP_DOL_HIPOT_mean',
'CANT_EMP_DOL_NEG_median',
'SALDO_DOLA_HIPOT_median',
'VAR_SALDO_DOLA_TOTAL_MA8_median',
'SALDO_DOLA_HIPOT_first',
'CANT_EMP_DOL_NEG_min',
'SALDO_DOLA_NEG_max',
'SALDO_DOLA_NEG_mean',
'SALDO_DOLA_NEG_last',
'CANT_EMP_DOL_HIPOT_median',
'SALDO_DOLA_HIPOT_last',
'SALDO_DOLA_HIPOT_mean',

 'PROXY_MOROSIDAD_1_mean',
 'PROXY_MOROSIDAD_1_median',
 'PROXY_MOROSIDAD_2_mean',
 'PROXY_MOROSIDAD_2_median',
 'PROXY_MOROSIDAD_3_mean',
 'PROXY_MOROSIDAD_3_median',
]
selected_cols = [col for col in data_train.columns if col not in unselected_cols]


data_train =  data_train.select_dtypes(include=['int64', 'float64', 'category'])
data_train = data_train[selected_cols]

data_sub = data_sub.select_dtypes(include=['int64', 'float64', 'category'])
data_sub = data_sub[selected_cols]

print(len(list(data_train.columns)))
print(data_train.dtypes)

356
TARGET                     int64
CO_TIPO_SEXO            category
EDAD                     float64
NO_DEPARTAMENTO         category
ANIO_BANCARIZACION       float64
                          ...   
SALDO_VENCIDO_202305     float64
SALDO_VENCIDO_202306     float64
SALDO_VENCIDO_202307     float64
SALDO_VENCIDO_202308     float64
SALDO_VENCIDO_202309     float64
Length: 356, dtype: object


In [6]:
data_train[TARGET_VAR].value_counts(normalize=True)

0   0.849992
1   0.150008
Name: TARGET, dtype: float64

In [8]:
import xgboost as xgb

def get_xgboost_model():
    return xgb.XGBClassifier(
        n_estimators=200, 
        max_depth=8, 
        learning_rate=0.1, 
        objective='binary:logistic', 
        booster='gbtree', 
        tree_method='auto', 
        n_jobs=-1, 
        verbosity=0, 
        enable_categorical=True,
        random_state=42
    )

def get_catboost_model(cat_features):
    # parameters found with optuna
    params = {
        'iterations': 998, 
        'depth': 8, 
        'learning_rate': 0.07471090640463454, 
        'random_strength': 8.956106045553469, 
        'bagging_temperature': 0.5576450661498814, 
        'border_count': 35, 
        'l2_leaf_reg': 48.29550360352743, 
        'scale_pos_weight': 1.007630313663112
    }
    return CatBoostClassifier(
        **params,
        loss_function='Logloss', 
        eval_metric='F1', 
        random_seed=42, 
        verbose=0, 
        cat_features=cat_features,
        thread_count=N_JOBS, 
        task_type='GPU', 
        devices='0:1',
    )


In [9]:
data_train[TARGET_VAR].value_counts()

0    77504
1    13678
Name: TARGET, dtype: int64

In [10]:
# random undersampling
from imblearn.under_sampling import RandomUnderSampler

rus = RandomUnderSampler(sampling_strategy={0: 50000}, random_state=42)
X_resampled, y_resampled = rus.fit_resample(data_train.drop(TARGET_VAR, axis=1), data_train[TARGET_VAR])

data_train_resampled = pd.concat([X_resampled, y_resampled], axis=1)

In [11]:
data_train_resampled[TARGET_VAR].value_counts(normalize=True)

0   0.826152
1   0.173848
Name: TARGET, dtype: float64

In [12]:
data_copy = data_train.copy()

X = data_train_resampled.drop(columns=[TARGET_VAR])
y = data_train_resampled[TARGET_VAR]
FACTOR = 0.39
cat_features = X.select_dtypes(include=['category']).columns.tolist()

In [ ]:

skf = StratifiedKFold(n_splits=N_FOLDS, shuffle=True, random_state=42)

f1_macros = []
for train_idx, test_idx in skf.split(X, y):
    cat_model = get_catboost_model(cat_features)
    X_train, X_test = X.iloc[train_idx], X.iloc[test_idx]
    y_train, y_test = y.iloc[train_idx], y.iloc[test_idx]

    cat_model.fit(X_train, y_train)
    y_pred = cat_model.predict_proba(X_test)[:, 1]
    y_pred = (y_pred > FACTOR).astype(int)
    print(classification_report(y_test, y_pred))
    
    f1_macros.append(f1_score(y_test, y_pred, average='macro'))

print(f'Mean F1 macro: {np.mean(f1_macros):.3f}')

In [14]:
X_train, X_test, y_train, y_test = train_test_split(
    X, 
    y, 
    test_size=0.2, 
    random_state=42, 
    stratify=y
)
cat_model = get_catboost_model(cat_features)
cat_model.fit(X, y)

# cat_model feature importance
importances = cat_model.feature_importances_
indices = np.argsort(importances)[::-1]


In [ ]:
# plot feature importance
plt.figure(figsize=(20, 10))
plt.title("Feature Importance")
plt.bar(range(X.shape[1]), importances[indices])
plt.xticks(range(X.shape[1]), X.columns[indices], rotation=90)
plt.show()

In [15]:
FACTOR = 0.39
data_copy['PRED'] = cat_model.predict_proba(data_copy.drop(columns=[TARGET_VAR]))[:, 1]
data_copy['PRED'] = (data_copy['PRED'] > FACTOR).astype(int)

data_sub['TARGET'] = cat_model.predict_proba(data_sub.drop(columns=[TARGET_VAR]))[:, 1]
data_sub['TARGET'] = (data_sub['TARGET'] > FACTOR).astype(int)

print(classification_report(data_copy[TARGET_VAR], data_copy['PRED']))

              precision    recall  f1-score   support

           0       0.95      0.95      0.95     77504
           1       0.70      0.69      0.69     13678

    accuracy                           0.91     91182
   macro avg       0.82      0.82      0.82     91182
weighted avg       0.91      0.91      0.91     91182



## Optuna version

Only run this part to find the best parameters, go to **Submission** section.
Don't run this section because it takes a long time to run.

In [23]:
from sklearn.metrics import f1_score, precision_score, recall_score

In [16]:
def objective_only_model_params(trial):
    params = {
        'iterations': trial.suggest_int('iterations', 100, 1000),
        'depth': trial.suggest_int('depth', 4, 10),
        'learning_rate': trial.suggest_float('learning_rate', 0.001, 0.1),
        'random_strength': trial.suggest_float('random_strength', 0.1, 10),
        'bagging_temperature': trial.suggest_float('bagging_temperature', 0.0, 1.0),
        'border_count': trial.suggest_int('border_count', 1, 255),
        'l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 1e-9, 100),
        'scale_pos_weight': trial.suggest_float('scale_pos_weight', 0.1, 10),
    }

    skf = StratifiedKFold(n_splits=N_FOLDS, shuffle=True, random_state=42)
    f1_macros = []

    for train_idx, test_idx in skf.split(X, y):
        cat_model = CatBoostClassifier(**params, cat_features=cat_features, task_type='GPU', devices='0:1')
        X_train, X_test = X.iloc[train_idx], X.iloc[test_idx]
        y_train, y_test = y.iloc[train_idx], y.iloc[test_idx]

        cat_model.fit(X_train, y_train)
        y_pred = cat_model.predict_proba(X_test)[:, 1]
        y_pred = (y_pred > FACTOR).astype(int)
        f1_macros.append(f1_score(y_test, y_pred, average='macro'))

    return np.mean(f1_macros)

def objective(trial):
        
    params = {
        'iterations': trial.suggest_int('iterations', 100, 1000),
        'depth': trial.suggest_int('depth', 4, 10),
        'learning_rate': trial.suggest_float('learning_rate', 0.001, 0.1),
        'random_strength': trial.suggest_float('random_strength', 0.1, 10),
        'bagging_temperature': trial.suggest_float('bagging_temperature', 0.0, 1.0),
        'border_count': trial.suggest_int('border_count', 1, 255),
        'l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 1e-9, 100),
        'scale_pos_weight': trial.suggest_float('scale_pos_weight', 0.1, 10),
    }

    factor = trial.suggest_float('factor', 0.1, 0.9)  # Uso de FACTOR como parámetro a optimizar
    skf = StratifiedKFold(n_splits=N_FOLDS, shuffle=True, random_state=42)
    f1_macros = []

    for train_idx, test_idx in skf.split(X, y):
        cat_model = CatBoostClassifier(**params, cat_features=cat_features)
        X_train, X_test = X.iloc[train_idx], X.iloc[test_idx]
        y_train, y_test = y.iloc[train_idx], y.iloc[test_idx]

        cat_model.fit(X_train, y_train)
        y_pred = cat_model.predict_proba(X_test)[:, 1]
        y_pred = (y_pred > factor).astype(int)
        f1_macros.append(f1_score(y_test, y_pred, average='macro'))

    return np.mean(f1_macros)

def objective_prec_recall(trial):
    params = {
        'iterations': trial.suggest_int('iterations', 100, 1000),
        'depth': trial.suggest_int('depth', 4, 10),
        'learning_rate': trial.suggest_float('learning_rate', 0.001, 0.1),
        'random_strength': trial.suggest_float('random_strength', 0.1, 10),
        'bagging_temperature': trial.suggest_float('bagging_temperature', 0.0, 1.0),
        'border_count': trial.suggest_int('border_count', 1, 255),
        'l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 1e-9, 100),
        'scale_pos_weight': trial.suggest_float('scale_pos_weight', 0.1, 10),
    }

    factor = trial.suggest_float('factor', 0.1, 0.9)  # Uso de FACTOR como parámetro a optimizar

    skf = StratifiedKFold(n_splits=N_FOLDS, shuffle=True, random_state=42)
    f1_macros = []
    precision_scores = []
    recall_scores = []

    for train_idx, test_idx in skf.split(X, y):
        cat_model = CatBoostClassifier(**params, cat_features=cat_features)
        X_train, X_test = X.iloc[train_idx], X.iloc[test_idx]
        y_train, y_test = y.iloc[train_idx], y.iloc[test_idx]

        cat_model.fit(X_train, y_train)
        y_pred = cat_model.predict_proba(X_test)[:, 1]
        y_pred_binary = (y_pred > factor).astype(int)
        
        f1_macros.append(f1_score(y_test, y_pred_binary, average='macro'))
        precision_scores.append(precision_score(y_test, y_pred_binary))
        recall_scores.append(recall_score(y_test, y_pred_binary))

    alpha = 0.5 
    weighted_precision_recall = alpha * np.mean(precision_scores) + (1 - alpha) * np.mean(recall_scores)

    weighted_f1 = np.mean(f1_macros) + weighted_precision_recall

    return weighted_f1

X = data_train_resampled.drop(columns=[TARGET_VAR])
y = data_train_resampled[TARGET_VAR]
cat_features = X.select_dtypes(include=['category']).columns.tolist()

study = optuna.create_study(direction='maximize')
study.optimize(objective_only_model_params, n_trials=50) 

best_params = study.best_params

best_cat_model = CatBoostClassifier(**best_params, cat_features=cat_features)
best_cat_model.fit(X, y)

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, stratify=y)
y_pred_test = best_cat_model.predict_proba(X_test)[:, 1]
y_pred_test = (y_pred_test > FACTOR).astype(int)

print("Classification Report (Test Data):")
print(classification_report(y_test, y_pred_test))

data_copy['PRED'] = best_cat_model.predict_proba(data_copy.drop(columns=[TARGET_VAR]))[:, 1]
data_copy['PRED'] = (data_copy['PRED'] > FACTOR).astype(int)

data_sub['TARGET'] = best_cat_model.predict_proba(data_sub.drop(columns=[TARGET_VAR]))[:, 1]
data_sub['TARGET'] = (data_sub['TARGET'] > FACTOR).astype(int)

print("Classification Report (Data Copy):")
print(classification_report(data_copy[TARGET_VAR], data_copy['PRED']))

[I 2023-11-19 21:35:33,463] A new study created in memory with name: no-name-d733eafb-a8ad-4aa2-9c7e-1a1eab82f044


0:	learn: 0.6540576	total: 93ms	remaining: 32.6s
1:	learn: 0.6280775	total: 182ms	remaining: 31.8s
2:	learn: 0.6044845	total: 269ms	remaining: 31.3s
3:	learn: 0.5863329	total: 353ms	remaining: 30.7s
4:	learn: 0.5736264	total: 438ms	remaining: 30.4s
5:	learn: 0.5629543	total: 527ms	remaining: 30.4s
6:	learn: 0.5524495	total: 615ms	remaining: 30.3s
7:	learn: 0.5437336	total: 694ms	remaining: 29.9s
8:	learn: 0.5380404	total: 773ms	remaining: 29.5s
9:	learn: 0.5329982	total: 855ms	remaining: 29.2s
10:	learn: 0.5288476	total: 937ms	remaining: 29.1s
11:	learn: 0.5244035	total: 1.04s	remaining: 29.5s
12:	learn: 0.5210372	total: 1.14s	remaining: 29.6s
13:	learn: 0.5173618	total: 1.22s	remaining: 29.5s
14:	learn: 0.5144577	total: 1.3s	remaining: 29.1s
15:	learn: 0.5119946	total: 1.37s	remaining: 28.9s
16:	learn: 0.5092752	total: 1.45s	remaining: 28.7s
17:	learn: 0.5062329	total: 1.54s	remaining: 28.6s
18:	learn: 0.5042525	total: 1.62s	remaining: 28.5s
19:	learn: 0.5022566	total: 1.7s	remaining:

[I 2023-11-19 21:38:05,427] Trial 0 finished with value: 0.6016609871768932 and parameters: {'iterations': 352, 'depth': 9, 'learning_rate': 0.09952290557547983, 'random_strength': 6.239286083122858, 'bagging_temperature': 0.4503352751598595, 'border_count': 50, 'l2_leaf_reg': 58.951110884921576, 'scale_pos_weight': 6.065130475055185}. Best is trial 0 with value: 0.6016609871768932.


0:	learn: 0.6448489	total: 474ms	remaining: 5m 23s
1:	learn: 0.6040061	total: 597ms	remaining: 3m 23s
2:	learn: 0.5683511	total: 714ms	remaining: 2m 41s
3:	learn: 0.5390047	total: 833ms	remaining: 2m 21s
4:	learn: 0.5147241	total: 958ms	remaining: 2m 9s
5:	learn: 0.4943713	total: 1.07s	remaining: 2m
6:	learn: 0.4749889	total: 1.19s	remaining: 1m 55s
7:	learn: 0.4592765	total: 1.3s	remaining: 1m 49s
8:	learn: 0.4487788	total: 1.41s	remaining: 1m 45s
9:	learn: 0.4378218	total: 1.53s	remaining: 1m 43s
10:	learn: 0.4295946	total: 1.65s	remaining: 1m 40s
11:	learn: 0.4221285	total: 1.77s	remaining: 1m 38s
12:	learn: 0.4163711	total: 1.89s	remaining: 1m 37s
13:	learn: 0.4104811	total: 2s	remaining: 1m 35s
14:	learn: 0.4043915	total: 2.12s	remaining: 1m 34s
15:	learn: 0.3993541	total: 2.23s	remaining: 1m 32s
16:	learn: 0.3957909	total: 2.35s	remaining: 1m 31s
17:	learn: 0.3922049	total: 2.46s	remaining: 1m 30s
18:	learn: 0.3883436	total: 2.58s	remaining: 1m 29s
19:	learn: 0.3853279	total: 2.7

[I 2023-11-19 21:44:54,110] Trial 1 finished with value: 0.7417137791243698 and parameters: {'iterations': 682, 'depth': 9, 'learning_rate': 0.07033788117653313, 'random_strength': 2.771815896651214, 'bagging_temperature': 0.23230316977818466, 'border_count': 180, 'l2_leaf_reg': 97.11920797436963, 'scale_pos_weight': 1.1531199853962788}. Best is trial 1 with value: 0.7417137791243698.


...

0:	learn: 0.6457519	total: 40.4ms	remaining: 18s
1:	learn: 0.6067470	total: 83.5ms	remaining: 18.6s
2:	learn: 0.5722128	total: 129ms	remaining: 19.1s
3:	learn: 0.5435144	total: 171ms	remaining: 18.9s
4:	learn: 0.5199236	total: 216ms	remaining: 19.1s
5:	learn: 0.4985178	total: 258ms	remaining: 19s
6:	learn: 0.4812027	total: 313ms	remaining: 19.7s
7:	learn: 0.4674072	total: 365ms	remaining: 20s
8:	learn: 0.4546056	total: 420ms	remaining: 20.4s
9:	learn: 0.4443371	total: 466ms	remaining: 20.4s
10:	learn: 0.4375409	total: 517ms	remaining: 20.5s
11:	learn: 0.4285446	total: 561ms	remaining: 20.3s
12:	learn: 0.4227689	total: 610ms	remaining: 20.4s
13:	learn: 0.4185656	total: 657ms	remaining: 20.3s
14:	learn: 0.4134931	total: 706ms	remaining: 20.3s
15:	learn: 0.4101874	total: 770ms	remaining: 20.8s
16:	learn: 0.4070807	total: 827ms	remaining: 20.9s
17:	learn: 0.4058905	total: 852ms	remaining: 20.3s
18:	learn: 0.4028084	total: 903ms	remaining: 20.3s
19:	learn: 0.4002095	total: 959ms	remaining: 

[I 2023-11-19 22:52:58,148] Trial 24 finished with value: 0.7391306213733222 and parameters: {'iterations': 447, 'depth': 7, 'learning_rate': 0.08243031264503052, 'random_strength': 5.515909859211894, 'bagging_temperature': 0.6268388563468464, 'border_count': 67, 'l2_leaf_reg': 76.83051097505758, 'scale_pos_weight': 1.2538147497058556}. Best is trial 20 with value: 0.7429903758327941.


0:	learn: 0.6446257	total: 239ms	remaining: 2m 34s
1:	learn: 0.6055193	total: 424ms	remaining: 2m 17s
2:	learn: 0.5717931	total: 595ms	remaining: 2m 7s
3:	learn: 0.5387137	total: 761ms	remaining: 2m 2s
4:	learn: 0.5132688	total: 928ms	remaining: 1m 59s
5:	learn: 0.4920541	total: 1s	remaining: 1m 47s
6:	learn: 0.4747791	total: 1.18s	remaining: 1m 47s
7:	learn: 0.4602745	total: 1.34s	remaining: 1m 47s
8:	learn: 0.4468980	total: 1.53s	remaining: 1m 48s
9:	learn: 0.4350148	total: 1.78s	remaining: 1m 53s
10:	learn: 0.4241299	total: 2s	remaining: 1m 55s
11:	learn: 0.4164279	total: 2.23s	remaining: 1m 58s
12:	learn: 0.4100427	total: 2.39s	remaining: 1m 56s
13:	learn: 0.4030745	total: 2.58s	remaining: 1m 56s
14:	learn: 0.3980298	total: 2.76s	remaining: 1m 56s
15:	learn: 0.3934163	total: 2.94s	remaining: 1m 56s
16:	learn: 0.3885140	total: 3.12s	remaining: 1m 55s
17:	learn: 0.3839684	total: 3.3s	remaining: 1m 55s
18:	learn: 0.3799671	total: 3.4s	remaining: 1m 52s
19:	learn: 0.3766883	total: 3.65

[I 2023-11-19 23:03:12,023] Trial 25 finished with value: 0.7420735907383353 and parameters: {'iterations': 648, 'depth': 10, 'learning_rate': 0.06479981564996601, 'random_strength': 3.9148851923253507, 'bagging_temperature': 0.40554729969307357, 'border_count': 144, 'l2_leaf_reg': 93.2301642361811, 'scale_pos_weight': 1.0287435521845527}. Best is trial 20 with value: 0.7429903758327941.


0:	learn: 0.6647339	total: 204ms	remaining: 2m 6s
1:	learn: 0.6403275	total: 440ms	remaining: 2m 16s
2:	learn: 0.6215377	total: 610ms	remaining: 2m 5s
3:	learn: 0.6028598	total: 781ms	remaining: 2m
4:	learn: 0.5883829	total: 953ms	remaining: 1m 57s
5:	learn: 0.5743086	total: 1.15s	remaining: 1m 58s
6:	learn: 0.5641581	total: 1.33s	remaining: 1m 57s
7:	learn: 0.5538081	total: 1.51s	remaining: 1m 56s
8:	learn: 0.5457008	total: 1.7s	remaining: 1m 55s
9:	learn: 0.5383649	total: 1.89s	remaining: 1m 55s
10:	learn: 0.5310363	total: 2.05s	remaining: 1m 53s
11:	learn: 0.5248959	total: 2.22s	remaining: 1m 52s
12:	learn: 0.5181920	total: 2.39s	remaining: 1m 51s
13:	learn: 0.5134838	total: 2.56s	remaining: 1m 51s
14:	learn: 0.5097734	total: 2.67s	remaining: 1m 48s
15:	learn: 0.5060402	total: 2.85s	remaining: 1m 47s
16:	learn: 0.5027570	total: 3.04s	remaining: 1m 48s
17:	learn: 0.4992637	total: 3.2s	remaining: 1m 47s
18:	learn: 0.4957623	total: 3.37s	remaining: 1m 46s
19:	learn: 0.4925367	total: 3.

## Subsmission

In [24]:
submission = pd.concat([data_sub_id, data_sub['TARGET']], axis=1)
print(submission['TARGET'].value_counts(normalize=True))

submission.to_csv('../data/results/catboost_all_resampled_optuna_3225_356_final_all_ds_under50k.csv', index=False)

0   0.852029
1   0.147971
Name: TARGET, dtype: float64
